# Minimum Working Example#

In [38]:
from netgen.csg import *
from netgen.occ import *
import numpy as np
from ngsolve import *
from ngsolve.solvers import *
from ngsolve.webgui import Draw
from Spectral_Representation import Tensor_Power

In [39]:
geo = Box((0,0,0), (3,0.6,1))
geo.faces.name="outer"
geo.faces.Min(X).name = "fix"

mesh = Mesh(OCCGeometry(geo).GenerateMesh(maxh=0.2)).Curve(3)


Draw (mesh);

WebGuiWidget(layout=Layout(height='50vh', width='100%'), value={'gui_settings': {}, 'ngsolve_version': '6.2.23…

In [43]:
E, nu = 210, 0.2
mu  = E / 2 / (1+nu)
lam = E * nu / ((1+nu)*(1-2*nu))

def F(u):
    return Id(3) + Grad(u)


Flag = 1

# 1   Tensor Power using Spectral representation
# 0   Eigenvalues using built in Eig()

def NeoHooke_FP(F):
    C= F.trans * F
    eig_C = C.Eig()
    if Flag:
        return 0.5*mu*((Trace(Tensor_Power(C, 1.0)) - 3) + 2*mu/lam*Det(C)**(-lam/2/mu)-1)
    else:
        return 0.5*mu*((eig_C[9] + eig_C[10] + eig_C[11] - 3) + 2*mu/lam*Det(C)**(-lam/2/mu)-1)

In [44]:
## Minimization Principle ##
fes = VectorH1(mesh, order=2, dirichlet="fix")
u,u_test = fes.TnT()


bforce = CF( (5,0,0) )

a = BilinearForm(fes, symmetric=True)
a += Variation(NeoHooke_FP(F(u)).Compile()*dx)
a += Variation(-(bforce*u).Compile()*dx)



In [45]:
## Newton Solver ##
gfsol = GridFunction(fes)
gfsol.vec[:] = 0

NewtonMinimization(a,gfsol,linesearch=False, maxit=8,maxerr=1e-8,inverse="pardiso",printing=True)


Draw (gfsol, mesh);

Newton iteration  0
Energy:  157.5000000000002
err =  0.7976067485716531
Newton iteration  1
Energy:  157.17438241063752
err =  0.03123950832597866
Newton iteration  2
Energy:  157.17389385542978
err =  6.054277979781416e-05
Newton iteration  3
Energy:  157.17389385359698
err =  3.1405356112290317e-10


WebGuiWidget(layout=Layout(height='50vh', width='100%'), value={'gui_settings': {}, 'ngsolve_version': '6.2.23…

In [30]:
## Postprocessing ##


fes_tfield = MatrixValued(L2(mesh, order=2))
F_pp = GridFunction(fes_tfield)
PK1_pp = GridFunction(fes_tfield)


_F = F(gfsol).MakeVariable()


F_pp.Interpolate(_F)


_PK1 = (NeoHooke_FP(_F)).Diff(_F)


PK1_pp.Interpolate(_PK1)






In [ ]:
## Own Linearization using Assemble ##

gfu = GridFunction(fes)

# Create a strain variable for partial differentiation
F_gf = F(gfu).MakeVariable()

# 1. PK stress
PK1 = NeoHooke_FP(F_gf).Diff(F_gf)


# elasticity tensor
cc = PK1.Diff(F_gf).Reshape((F_gf.dim, F_gf.dim))

# reshape test and trial strians
delta_eps = F(u_test).Reshape((F_gf.dim, ))
Delta_eps = F(u).Reshape((F_gf.dim, ))

## Bilinear Form ##
bf = BilinearForm(fes, symmetric=True)
bf += InnerProduct(delta_eps, cc * Delta_eps).Compile() * dx

bf.Assemble()